In [1]:
%load_ext rpy2.ipython

In [2]:
%%R
set.seed(88888888) # maximum luck

library(DESeq2)
library(plotly)
library(ggplot2)
library(viridis)
library(magrittr)
library(pheatmap)
library(DescTools)
library(pdfCluster)
library(RColorBrewer)
library(SummarizedExperiment)
library(caret)
library(class)
library(htmlwidgets)

Loading required package: S4Vectors
Loading required package: stats4
Loading required package: BiocGenerics

Attaching package: ‘BiocGenerics’

The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs

The following objects are masked from ‘package:base’:

    anyDuplicated, aperm, append, as.data.frame, basename, cbind,
    colnames, dirname, do.call, duplicated, eval, evalq, Filter, Find,
    get, grep, grepl, intersect, is.unsorted, lapply, Map, mapply,
    match, mget, order, paste, pmax, pmax.int, pmin, pmin.int,
    Position, rank, rbind, Reduce, rownames, sapply, setdiff, sort,
    table, tapply, union, unique, unsplit, which.max, which.min


Attaching package: ‘S4Vectors’

The following object is masked from ‘package:utils’:

    findMatches

The following objects are masked from ‘package:base’:

    expand.grid, I, unname

Loading required package: IRanges
Loading required package: GenomicRanges
Loading required package: GenomeInfoDb
Loading require

In [3]:
%%R
OUT_DIR <- "/mnt/home/yuankeji/RanceLab/reticula_new/reticula/data/tcdd/output/"
N_FOLDS <- 10

In [4]:
%%R
vst.counts <- readRDS(paste(OUT_DIR, "vst_counts0.03vs30_time_cross.Rds", sep = ""))
print(vst.counts)

class: DESeqTransform 
dim: 9297 91 
metadata(1): version
assays(1): ''
rownames(9297): ENSMUSG00000000001 ENSMUSG00000000028 ...
  ENSMUSG00000118462 ENSMUSG00000118541
rowData names(4): baseMean baseVar allZero dispFit
colnames(91): SRR7817617 SRR7817618 ... SRR4317659 SRR4317660
colData names(3): Sample Dose sizeFactor


In [5]:
%%R
sample <- colData(vst.counts)
# print(sample)

In [6]:
%%R
vst.count.mtx <-
   vst.counts %>% SummarizedExperiment::assay() %>% as.data.frame()

In [7]:
%%R
tcdd_dose_detail.vec <-
   readRDS(paste(OUT_DIR, "tcdd_dose_detail_vec0.03vs30_time_cross.Rds", sep = ""))
print(tcdd_dose_detail.vec)

 [1] 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00
[13] 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00
[25] 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00
[37] 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00
[49]  0.03  0.03  0.03  0.03  0.03  0.03  0.03  0.03  0.03  0.03  0.03 30.00
[61] 30.00 30.00 30.00 30.00 30.00  0.03  0.03  0.03  0.03  0.03  0.03 30.00
[73] 30.00 30.00 30.00 30.00 30.00 30.00 30.00  0.03  0.03  0.03  0.03  0.03
[85]  0.03 30.00 30.00 30.00 30.00 30.00 30.00


In [8]:
%%R
rxn2ensembls.nls <-
   readRDS(paste(OUT_DIR, "rxn2ensembls_nls0.03vs30_time_cross.Rds", sep = ""))
print(length(rxn2ensembls.nls))
print(rxn2ensembls.nls)

[1] 9825
$`R-MMU-170666`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170671`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170674`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSM

 [46] "ENSMUSG00000028777" "ENSMUSG00000028950" "ENSMUSG00000028971"
 [49] "ENSMUSG00000029064" "ENSMUSG00000029072" "ENSMUSG00000029236"
 [52] "ENSMUSG00000029371" "ENSMUSG00000029372" "ENSMUSG00000029373"
 [55] "ENSMUSG00000029379" "ENSMUSG00000029380" "ENSMUSG00000029417"
 [58] "ENSMUSG00000029530" "ENSMUSG00000029663" "ENSMUSG00000029713"
 [61] "ENSMUSG00000029819" "ENSMUSG00000031778" "ENSMUSG00000031861"
 [64] "ENSMUSG00000031980" "ENSMUSG00000032192" "ENSMUSG00000032562"
 [67] "ENSMUSG00000032766" "ENSMUSG00000033717" "ENSMUSG00000034117"
 [70] "ENSMUSG00000034855" "ENSMUSG00000035042" "ENSMUSG00000035383"
 [73] "ENSMUSG00000035431" "ENSMUSG00000035448" "ENSMUSG00000036353"
 [76] "ENSMUSG00000036362" "ENSMUSG00000036381" "ENSMUSG00000036402"
 [79] "ENSMUSG00000036437" "ENSMUSG00000036832" "ENSMUSG00000037010"
 [82] "ENSMUSG00000037014" "ENSMUSG00000037140" "ENSMUSG00000037346"
 [85] "ENSMUSG00000037944" "ENSMUSG00000038607" "ENSMUSG00000038668"
 [88] "ENSMUSG00000038811" "ENSMUS

 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982019`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982020`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUS

 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000024325" "ENSMUSG00000025577" "ENSMUSG00000025578"
 [7] "ENSMUSG00000026021" "ENSMUSG00000026484" "ENSMUSG00000026739"
[10] "ENSMUSG00000028796" "ENSMUSG00000037652" "ENSMUSG00000039989"
[13] "ENSMUSG00000040669"

$`R-MMU-4570463`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020265" "ENSMUSG00000020738" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000031347"
[13] "ENSMUSG00000037652" "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MMU-4570499`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020738" "ENSMUSG00000021546" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000037652"
[13] "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MM

 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-3781943`
 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-205328`
[1] "ENSMUSG00000000127" "ENSMUSG00000005672" "ENSMUSG00000019966"
[4] "ENSMUSG00000032113" "ENSM

...

$`R-MMU-2395965`
[1] "ENSMUSG00000045211"

$`R-MMU-444848`
[1] "ENSMUSG00000045232" "ENSMUSG00000060735"

$`R-MMU-444859`
[1] "ENSMUSG00000045232" "ENSMUSG00000049741" "ENSMUSG00000066090"

$`R-MMU-8874435`
[1] "ENSMUSG00000045282"

$`R-MMU-9012016`
[1] "ENSMUSG00000045316"

$`R-MMU-1679589`
[1] "ENSMUSG00000045322"

$`R-MMU-9679045`
[1] "ENSMUSG00000045322"

$`R-MMU-984689`
[1] "ENSMUSG00000045328"

$`R-MMU-8867240`
[1] "ENSMUSG00000045394"

$`R-MMU-1299297`
[1] "ENSMUSG00000045404"

$`R-MMU-3296309`
[1] "ENSMUSG00000045502"

$`R-MMU-444661`
[1] "ENSMUSG00000045502"

$`R-MMU-9613570`
[1] "ENSMUSG00000045534"

$`R-MMU-444527`
[1] "ENSMUSG00000045551"

$`R-MMU-9704297`
[1] "ENSMUSG00000045613"

$`R-MMU-162797`
[1] "ENSMUSG00000045625"

$`R-MMU-965067`
[1] "ENSMUSG00000045691"

$`R-NUL-421961`
[1] "ENSMUSG00000045730"

$`R-MMU-9634846`
[1] "ENSMUSG00000045903" "ENSMUSG00000055116"

$`R-MMU-9639576`
[1] "ENSMUSG00000045903"

$`R-MMU-9640074`
[1] "ENSMUSG00000045903"

$`R-MMU-9769840`
[1] 

[1] "ENSMUSG00000051212"

$`R-MMU-444171`
[1] "ENSMUSG00000051314"

$`R-MMU-9831007`
[1] "ENSMUSG00000051367" "ENSMUSG00000074934"

$`R-MMU-8869694`
[1] "ENSMUSG00000051439"

$`R-MMU-2161651`
[1] "ENSMUSG00000051483"

$`R-MMU-9729538`
[1] "ENSMUSG00000051596"

$`R-MMU-912383`
[1] "ENSMUSG00000051977"

$`R-NUL-1214205`
[1] "ENSMUSG00000051977"

$`R-MMU-420724`
[1] "ENSMUSG00000051980"

$`R-MMU-9703895`
[1] "ENSMUSG00000051980"

$`R-MMU-444100`
[1] "ENSMUSG00000052026"

$`R-NUL-9622751`
[1] "ENSMUSG00000052135"

$`R-NUL-9622814`
[1] "ENSMUSG00000052135"

$`R-MMU-391937`
[1] "ENSMUSG00000052229"

$`R-MMU-418918`
[1] "ENSMUSG00000052229"

$`R-MMU-1237325`
[1] "ENSMUSG00000052305" "ENSMUSG00000069919" "ENSMUSG00000073940"

$`R-MMU-1247668`
[1] "ENSMUSG00000052305" "ENSMUSG00000069919" "ENSMUSG00000073940"

$`R-MMU-9707504`
[1] "ENSMUSG00000052305" "ENSMUSG00000069919" "ENSMUSG00000073940"

$`R-MMU-9707516`
[1] "ENSMUSG00000052305" "ENSMUSG00000069919" "ENSMUSG00000073940"

$`R-MMU-9709317`


 [4] "ENSMUSG00000060678" "ENSMUSG00000060981" "ENSMUSG00000061482"
 [7] "ENSMUSG00000064288" "ENSMUSG00000067455" "ENSMUSG00000069266"
[10] "ENSMUSG00000069274" "ENSMUSG00000069305" "ENSMUSG00000069306"
[13] "ENSMUSG00000091405" "ENSMUSG00000096010"

$`R-MMU-5661125`
 [1] "ENSMUSG00000056962" "ENSMUSG00000060093" "ENSMUSG00000060639"
 [4] "ENSMUSG00000060678" "ENSMUSG00000060981" "ENSMUSG00000061482"
 [7] "ENSMUSG00000064288" "ENSMUSG00000067455" "ENSMUSG00000069266"
[10] "ENSMUSG00000069274" "ENSMUSG00000069305" "ENSMUSG00000069306"
[13] "ENSMUSG00000091405" "ENSMUSG00000096010"

$`R-MMU-9619024`
[1] "ENSMUSG00000056973"

$`R-MMU-9727567`
[1] "ENSMUSG00000056973"

$`R-MMU-6814153`
[1] "ENSMUSG00000057134"

$`R-MMU-508561`
[1] "ENSMUSG00000057228"

$`R-MMU-70952`
[1] "ENSMUSG00000057228"

$`R-MMU-893583`
[1] "ENSMUSG00000057228"

$`R-NUL-2467624`
[1] "ENSMUSG00000057280"

$`R-MMU-9692376`
[1] "ENSMUSG00000057329"

$`R-MMU-9695917`
[1] "ENSMUSG00000057342"

$`R-MMU-9695949`
[1] "ENSMUS

[1] "ENSMUSG00000063235"

$`R-MMU-351947`
[1] "ENSMUSG00000063410"

$`R-MMU-6810076`
[1] "ENSMUSG00000063428"

$`R-MMU-70577`
[1] "ENSMUSG00000063445" "ENSMUSG00000076441"

$`R-MMU-3204311`
[1] "ENSMUSG00000063558"

$`R-MMU-8944220`
[1] "ENSMUSG00000063564"

$`R-NUL-2473498`
[1] "ENSMUSG00000063564"

$`R-MMU-159566`
[1] "ENSMUSG00000063683" "ENSMUSG00000091043"

$`R-MMU-159574`
[1] "ENSMUSG00000063683" "ENSMUSG00000091043"

$`R-MMU-9750001`
[1] "ENSMUSG00000063683" "ENSMUSG00000091043"

$`R-MMU-9794643`
[1] "ENSMUSG00000063796"

$`R-MMU-196840`
[1] "ENSMUSG00000063849"

$`R-MMU-3323013`
[1] "ENSMUSG00000063856"

$`R-MMU-71676`
[1] "ENSMUSG00000063856"

$`R-MMU-8850831`
[1] "ENSMUSG00000064023"

$`R-MMU-947535`
[1] "ENSMUSG00000064120"

$`R-MMU-422017`
[1] "ENSMUSG00000064177" "ENSMUSG00000071113"

$`R-MMU-422104`
[1] "ENSMUSG00000064177" "ENSMUSG00000071113"

$`R-MMU-2534378`
[1] "ENSMUSG00000064267"

$`R-MMU-6788999`
[1] "ENSMUSG00000064267"

$`R-MMU-444654`
[1] "ENSMUSG00000064272"



IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [9]:
%%R
rxns <- rxn2ensembls.nls %>% names()

In [10]:
%%R
rxn_knn_misclass_rate.nls <- list()
rxn_knn_ari.nls <- list()
rxn_knn_ecount.nls <- list()
rxn_pca.nls <- list()
count <- 0

In [11]:
%%R
toi_indices <- seq(1,length(tcdd_dose_detail.vec))
print(toi_indices)

 [1]  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25
[26] 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50
[51] 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75
[76] 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91


In [12]:
%%R
tcdd_dose_detail_vec_tis_of_interest <-
   tcdd_dose_detail.vec[toi_indices]
print(tcdd_dose_detail_vec_tis_of_interest)

 [1] 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00
[13] 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00
[25] 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00
[37] 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00 30.00
[49]  0.03  0.03  0.03  0.03  0.03  0.03  0.03  0.03  0.03  0.03  0.03 30.00
[61] 30.00 30.00 30.00 30.00 30.00  0.03  0.03  0.03  0.03  0.03  0.03 30.00
[73] 30.00 30.00 30.00 30.00 30.00 30.00 30.00  0.03  0.03  0.03  0.03  0.03
[85]  0.03 30.00 30.00 30.00 30.00 30.00 30.00


In [13]:
%%R
vst.count.mtx.tis_of_interest <- vst.count.mtx[, toi_indices]
print(vst.count.mtx.tis_of_interest)

                   SRR7817617 SRR7817618 SRR7817619 SRR7817620 SRR7817621
ENSMUSG00000000001   19.00085   19.05143   20.51959   20.50590   20.12617
ENSMUSG00000000028   14.48679   14.25969   14.15300   14.44303   13.65971
ENSMUSG00000000049   22.76727   22.76739   21.78069   21.74323   21.29666
ENSMUSG00000000058   13.68812   13.58177   14.87094   14.88482   15.85656
ENSMUSG00000000085   16.13501   16.23586   15.72814   15.99052   15.90647
ENSMUSG00000000088   21.82339   21.83776   20.65580   20.65829   20.58019
ENSMUSG00000000120   13.79087   13.49688   14.64485   14.83223   14.26440
ENSMUSG00000000126   11.71590   12.17201   11.75577   12.23018   12.88930
ENSMUSG00000000127   13.75173   13.97324   14.17307   13.83034   14.29369
ENSMUSG00000000142   14.81684   14.87809   16.58083   16.33906   15.94887
ENSMUSG00000000149   19.42672   19.58054   19.63772   19.58663   19.61802
ENSMUSG00000000154   20.18999   20.23147   19.28482   19.28012   18.87479
ENSMUSG00000000168   17.85113   18.006

ENSMUSG00000001105   17.85393   17.88410   16.63582   16.68703   17.21000
ENSMUSG00000001119   16.70211   16.68155   16.72504   16.74319   18.05396
ENSMUSG00000001123   21.23914   21.20196   20.98565   20.93843   20.17189
ENSMUSG00000001127   19.22116   19.32006   19.23034   19.30936   19.15226
ENSMUSG00000001128   18.69936   18.82145   16.99691   16.91010   17.60265
ENSMUSG00000001131   15.64099   15.68680   13.73752   13.82367   15.54273
ENSMUSG00000001143   15.37890   15.37963   15.25434   15.45955   14.77949
ENSMUSG00000001155   20.57872   20.60693   20.13845   20.13355   19.79460
ENSMUSG00000001158   17.21281   17.30107   16.15991   16.10207   16.19913
ENSMUSG00000001173   14.24209   14.44037   15.67176   15.72302   16.28434
ENSMUSG00000001175   21.11785   21.11093   20.87351   20.89571   21.01865
ENSMUSG00000001211   21.96925   21.97048   21.35804   21.38297   21.18323
ENSMUSG00000001225   11.12690   11.12685   11.68350   11.12391   11.12083
ENSMUSG00000001228   14.15168   14.120

ENSMUSG00000002249   14.65645   14.56746   14.67592   14.82244   15.17450
ENSMUSG00000002250   16.38782   16.72976   16.10386   16.14511   16.90709
ENSMUSG00000002257   13.49596   13.87016   13.09336   13.13759   13.62420
ENSMUSG00000002279   18.86091   18.75557   17.58480   17.51266   17.16952
ENSMUSG00000002289   20.12812   20.15130   19.48087   19.56362   19.97514
ENSMUSG00000002297   15.89519   15.74322   16.08944   16.18946   16.18261
ENSMUSG00000002307   16.28518   16.27099   16.12857   16.18407   16.31086
ENSMUSG00000002308   14.26457   14.87346   13.68449   13.60968   14.04240
ENSMUSG00000002324   13.51451   14.04853   12.37097   12.78269   13.09309
ENSMUSG00000002325   15.86402   15.98112   16.19334   16.02769   15.63279
ENSMUSG00000002326   18.01820   17.84304   16.88953   17.11273   16.72473
ENSMUSG00000002346   17.73874   17.79116   18.34054   18.57694   17.60293
ENSMUSG00000002365   17.85187   17.97974   18.30868   18.26678   18.26494
ENSMUSG00000002379   20.20123   20.186

ENSMUSG00000003379   14.16919   14.14484   13.22097   13.11891   13.07334
ENSMUSG00000003402   21.47321   21.41321   20.09244   20.00367   19.71705
ENSMUSG00000003411   15.39480   15.22855   14.39969   14.30824   14.35306
ENSMUSG00000003418   11.91293   11.71525   12.11612   12.00072   12.57698
ENSMUSG00000003421   18.20176   18.15200   16.91392   16.54764   17.03890
ENSMUSG00000003429   20.58663   20.66350   18.81624   18.85815   19.02127
ENSMUSG00000003435   19.12242   19.24071   18.57331   18.68802   18.84972
ENSMUSG00000003436   11.12690   11.12685   11.12417   11.12391   11.12083
ENSMUSG00000003437   18.51497   18.53466   17.08853   17.21868   17.34246
ENSMUSG00000003444   15.55500   15.44920   13.76183   13.51233   13.84134
ENSMUSG00000003452   12.27432   12.05518   12.20798   12.68357   13.42110
ENSMUSG00000003458   18.06332   18.12319   18.67399   18.77551   18.74472
ENSMUSG00000003464   20.08660   20.04675   20.27962   20.32061   20.18417
ENSMUSG00000003476   11.12690   11.126

ENSMUSG00000005107   13.71569   13.60003   14.11944   14.06513   16.10557
ENSMUSG00000005142   20.58449   20.63310   20.28447   20.24743   20.70062
ENSMUSG00000005148   12.34271   12.26455   13.55382   13.25124   12.38633
ENSMUSG00000005150   17.27846   17.19251   16.94818   16.87859   17.42821
ENSMUSG00000005161   19.21875   19.20273   19.22845   19.17998   19.68776
ENSMUSG00000005198   18.50558   18.57771   18.33137   18.46888   17.35526
ENSMUSG00000005204   18.27603   18.23047   18.34373   18.17382   18.41742
ENSMUSG00000005220   13.02114   12.67937   12.44798   12.70677   12.68921
ENSMUSG00000005225   17.87354   17.77301   17.81486   17.90159   18.39574
ENSMUSG00000005232   11.84822   11.84742   11.65785   11.12182   11.12778
ENSMUSG00000005233   16.45755   16.20355   16.03425   15.98199   15.41076
ENSMUSG00000005262   18.43358   18.44381   18.69493   18.58035   18.67001
ENSMUSG00000005268   15.50860   15.51925   14.28951   14.49653   20.52037
ENSMUSG00000005299   18.99543   18.968

...

ENSMUSG00000016524   11.13482   11.13170   11.13216   11.12945   11.12996
ENSMUSG00000016528   19.50485   19.18095   19.29578   19.32606   19.32331
ENSMUSG00000016529   11.13482   11.13170   11.13216   11.12945   11.12996
ENSMUSG00000016534   23.01833   23.21196   23.21692   23.12000   23.12824
ENSMUSG00000016554   19.25782   19.15173   19.19741   19.33637   19.39188
ENSMUSG00000016559   20.14533   20.39332   20.41523   20.22194   20.09566
ENSMUSG00000016619   17.96829   18.07606   17.97412   18.00128   18.05478
ENSMUSG00000016637   15.70632   15.71465   15.70169   15.32485   15.34549
ENSMUSG00000016664   18.03177   18.30297   18.27352   18.63426   18.62581
ENSMUSG00000016757   15.74357   15.37528   15.08447   15.38489   15.40762
ENSMUSG00000016763   11.80882   11.77232   11.77772   11.12945   12.50822
ENSMUSG00000016833   17.36033   17.40906   17.39847   16.97454   17.17653
ENSMUSG00000016933   18.75291   18.91255   18.96950   19.32741   19.25468
ENSMUSG00000016942   22.34221   22.137

ENSMUSG00000000120   12.56502   12.71145   13.11811   12.68138   13.50700
ENSMUSG00000000126   12.03609   12.43709   12.13973   12.24958   12.56507
ENSMUSG00000000127   13.87481   14.13323   14.04006   14.24844   14.17259
ENSMUSG00000000142   16.46827   16.63844   17.08972   17.14508   17.30791
ENSMUSG00000000149   19.21470   19.20546   19.70319   19.63974   19.66600
ENSMUSG00000000154   18.67437   18.66206   18.85035   18.92759   19.20452
ENSMUSG00000000168   18.41065   18.43371   18.28086   18.36475   17.81118
ENSMUSG00000000171   20.65093   20.62642   20.76810   20.77674   20.33581
ENSMUSG00000000182   12.41625   12.21579   12.02650   11.89275   12.00820
ENSMUSG00000000183   11.70469   11.11441   11.12530   11.12582   11.62262
ENSMUSG00000000184   16.40567   16.34993   16.84419   16.60594   16.67901
ENSMUSG00000000197   11.56141   11.53692   11.88767   11.12582   11.11906
ENSMUSG00000000214   11.11398   11.11441   11.12530   11.12582   11.11906
ENSMUSG00000000215   11.11398   11.114

ENSMUSG00000001155   19.32039   19.32303   20.09967   19.98201   19.71669
ENSMUSG00000001158   15.95450   16.23682   15.90523   15.87168   16.17227
ENSMUSG00000001173   16.14731   16.21683   15.63937   15.89073   16.20436
ENSMUSG00000001175   20.09973   20.09480   19.79139   19.77977   20.09058
ENSMUSG00000001211   20.90130   20.87732   21.35982   21.32835   21.20562
ENSMUSG00000001225   11.11398   11.56665   11.12530   11.12582   11.11906
ENSMUSG00000001228   13.50119   13.47273   14.01187   13.81676   13.48574
ENSMUSG00000001240   19.24169   19.22562   18.99926   19.14466   19.00508
ENSMUSG00000001247   18.51948   18.46349   19.08676   19.07481   19.51396
ENSMUSG00000001249   20.85631   20.87129   21.44283   21.39315   21.17636
ENSMUSG00000001270   14.80399   14.50430   14.35163   14.40261   15.26437
ENSMUSG00000001280   18.11118   18.02593   18.15643   18.21456   18.20802
ENSMUSG00000001281   14.49408   14.46808   14.35540   13.91872   15.35951
ENSMUSG00000001288   15.50593   15.138

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)




ENSMUSG00000003617   22.65645   22.66448   22.73142   22.74596   22.17035
ENSMUSG00000003623   21.90290   21.86508   23.12261   23.09827   22.38750
ENSMUSG00000003644   16.38624   16.59223   16.70356   16.75148   17.28092
ENSMUSG00000003660   19.35031   19.34267   19.66100   19.58793   19.59566
ENSMUSG00000003665   11.80715   11.81558   11.12530   11.12582   11.11906
ENSMUSG00000003731   19.17316   19.21003   19.23933   19.30598   19.04868
ENSMUSG00000003746   20.87322   20.86243   21.60686   21.56794   21.39898
ENSMUSG00000003752   15.04779   14.90100   15.27655   15.23704   15.28722
ENSMUSG00000003779   14.64577   14.67964   14.72214   14.95583   15.29095
ENSMUSG00000003809   20.97107   20.97589   21.72869   21.69448   21.27463
ENSMUSG00000003812   17.57519   17.73074   17.74811   17.92740   17.98460
ENSMUSG00000003813   18.28612   18.22305   18.53227   18.61796   18.77227
ENSMUSG00000003814   21.36768   21.36888   21.92326   21.90660   22.37887
ENSMUSG00000003824   13.55814   13.40

In [14]:
%%R
training_indices <-
   caret::createDataPartition(
      tcdd_dose_detail_vec_tis_of_interest,
      times = 1,
      p = 1.0, # no data will be held out when set to "1.0"
      list = FALSE
   )
print(training_indices)

In [15]:
%%R
vst.count.mtx.train <-
   vst.count.mtx.tis_of_interest[, training_indices] #9/10ths of data
vst.count.mtx.test  <-
   vst.count.mtx.tis_of_interest[, -training_indices] #1/10th of data

print(vst.count.mtx.train)


ENSMUSG00000000903   11.12054   12.17933   12.25821   11.96591   12.07022
ENSMUSG00000000915   17.87907   17.51356   17.56950   17.78356   17.55554
ENSMUSG00000000942   12.75148   12.33221   12.45269   12.56266   12.71451
ENSMUSG00000000957   18.99632   18.39447   18.39147   18.44714   18.43488
ENSMUSG00000000958   15.21507   14.54423   14.66498   15.17470   14.86331
ENSMUSG00000000959   18.24888   18.10269   18.18275   18.42850   18.48743
ENSMUSG00000000982   14.29042   13.56244   13.27218   13.72650   13.86230
ENSMUSG00000001014   11.64026   12.08675   11.97679   11.83613   11.83505
ENSMUSG00000001016   16.26971   16.13835   16.37557   15.97282   16.20786
ENSMUSG00000001017   18.10753   18.19278   18.20570   18.31938   18.24229
ENSMUSG00000001018   17.27830   16.51412   16.81417   16.89279   16.85975
ENSMUSG00000001029   14.63645   14.38417   14.49999   14.93222   14.65115
ENSMUSG00000001034   15.81948   15.09355   15.29261   15.50681   15.72853
ENSMUSG00000001036   17.12671   15.75

ENSMUSG00000004317   16.71108   15.78672   15.89064   16.06597   16.12590
ENSMUSG00000004319   18.84954   19.14491   19.28245   18.90441   18.96464
ENSMUSG00000004328   13.06002   12.26163   12.25821   12.36420   12.16120
ENSMUSG00000004341   11.12054   11.84757   11.12263   11.12205   11.12198
ENSMUSG00000004344   11.12054   11.12277   11.12263   11.12205   11.12198
ENSMUSG00000004347   12.56806   12.52938   12.25664   12.31736   12.24203
ENSMUSG00000004356   16.87326   17.30062   17.50357   17.08204   17.08445
ENSMUSG00000004364   18.84839   18.84178   18.96440   19.01639   19.01497
ENSMUSG00000004366   11.12054   11.12277   11.12263   11.12205   11.12198
ENSMUSG00000004371   11.99883   11.12277   11.66522   11.96591   11.12198
ENSMUSG00000004383   14.61944   13.84907   13.68477   13.78006   14.39895
ENSMUSG00000004415   11.12054   11.12277   11.12263   11.12205   11.12198
ENSMUSG00000004446   15.69143   15.27247   15.11258   15.02855   14.98258
ENSMUSG00000004455   16.03603   16.000

ENSMUSG00000005469   17.40817   17.15089   17.30951   17.15607   17.10962
ENSMUSG00000005474   11.12054   11.12277   11.12263   11.12205   11.12198
ENSMUSG00000005481   17.72378   17.29199   17.37003   17.72731   17.66538
ENSMUSG00000005483   16.09725   16.51249   16.45504   16.50471   16.59542
ENSMUSG00000005493   11.12054   11.84757   11.66522   11.83019   11.12198
ENSMUSG00000005510   18.85795   18.54358   18.56907   18.40724   18.37301
ENSMUSG00000005533   14.94105   14.87813   14.69215   14.99088   14.56291
ENSMUSG00000005534   18.87761   19.36931   19.37213   18.87034   18.96650
ENSMUSG00000005547   24.16435   25.58308   25.58827   25.24836   25.25556
ENSMUSG00000005553   11.64026   11.12277   11.66522   11.12205   11.65751
ENSMUSG00000005566   18.81491   18.61819   18.66118   18.73228   18.73203
ENSMUSG00000005575   18.92989   18.51132   18.53521   18.82040   18.85399
ENSMUSG00000005580   15.09845   15.43245   15.56990   15.62810   15.21569
ENSMUSG00000005583   14.67573   15.000

ENSMUSG00000006611   18.72082   19.05849   19.11512   18.93514   18.78752
ENSMUSG00000006641   14.33580   14.93719   14.94457   14.39379   14.32697
ENSMUSG00000006649   11.80901   11.12277   11.84539   12.16276   11.83505
ENSMUSG00000006676   19.43822   19.64197   19.77123   19.73877   19.66249
ENSMUSG00000006678   14.41419   14.49563   14.43105   14.50300   14.56516
ENSMUSG00000006699   20.72794   20.28444   20.26266   20.63669   20.67497
ENSMUSG00000006705   15.97300   16.00730   15.77804   16.15103   16.22346
ENSMUSG00000006711   12.52766   12.88255   12.54974   12.53112   12.37034
ENSMUSG00000006715   17.04786   17.63474   17.64709   17.25157   17.09078
ENSMUSG00000006717   16.57087   17.12570   17.07178   16.27314   16.36529
ENSMUSG00000006720   13.18763   12.47072   12.33288   12.31167   12.37034
ENSMUSG00000006724   12.12767   11.66685   11.76765   11.65831   12.16120
ENSMUSG00000006728   19.60284   20.29064   20.27026   19.28481   19.35541
ENSMUSG00000006731   18.25799   17.488

ENSMUSG00000009406   14.57206   14.60463   14.52318   14.31449   13.97708
ENSMUSG00000009470   19.38581   18.98955   19.17164   19.27531   19.34823
ENSMUSG00000009487   11.12054   11.12277   11.12263   11.12205   11.12198
ENSMUSG00000009535   17.34410   17.01115   17.01133   17.26938   17.37362
ENSMUSG00000009545   13.96172   12.91469   12.81420   12.95319   13.19320
ENSMUSG00000009549   18.52566   18.15106   18.20348   18.32664   18.34404
ENSMUSG00000009555   18.13033   17.63315   17.59037   18.13620   18.08841
ENSMUSG00000009566   18.90464   19.62438   19.59249   18.49930   18.43866
ENSMUSG00000009575   18.01762   17.52587   17.55137   17.42611   17.47946
ENSMUSG00000009585   15.91620   15.42386   15.26715   16.15288   16.20906
ENSMUSG00000009588   11.12054   11.12277   11.12263   11.12205   11.65751
ENSMUSG00000009614   16.95103   18.31587   18.15213   16.85705   16.90592
ENSMUSG00000009621   17.82714   18.12296   18.20066   17.88586   17.93461
ENSMUSG00000009630   18.17607   17.412

...

ENSMUSG00000007207   12.83275   12.73655   12.66050   12.59094   12.77477
ENSMUSG00000007216   14.02796   13.69462   13.42530   13.42320   12.98795
ENSMUSG00000007279   11.13506   11.12741   11.14387   11.12305   11.13506
ENSMUSG00000007338   17.82115   17.26947   17.26341   17.37448   17.81066
ENSMUSG00000007379   13.41900   13.94377   13.73630   13.73315   13.11264
ENSMUSG00000007411   17.87202   17.94972   17.79201   18.06515   18.00404
ENSMUSG00000007458   19.69839   20.38417   20.42693   20.45977   19.72553
ENSMUSG00000007476   17.64793   17.84510   18.03966   17.79865   17.87003
ENSMUSG00000007480   11.13506   11.12741   15.73773   15.82645   16.00157
ENSMUSG00000016194   18.04646   18.21303   19.94892   19.87170   20.43278
ENSMUSG00000016206   14.17079   14.03981   14.23416   13.84206   14.13385
ENSMUSG00000016252   19.19761   19.18863   19.04030   19.06633   17.76862
ENSMUSG00000016253   16.54245   16.54907   17.02012   16.78503   16.67168
ENSMUSG00000016255   11.70228   11.566

ENSMUSG00000017929   17.56783   17.50860   17.23641   17.04124   17.28330
ENSMUSG00000017950   22.28129   22.29576   22.61843   22.61623   22.49264
ENSMUSG00000017969   13.87370   13.90454   13.85252   13.91391   14.16998
ENSMUSG00000018001   16.31292   16.04934   15.74129   15.84809   16.56056
ENSMUSG00000018008   16.56825   16.79418   16.52853   16.52384   17.57295
ENSMUSG00000018012   13.28838   13.12947   13.85144   13.94959   13.69104
ENSMUSG00000018040   17.20431   17.31337   17.17439   17.14128   17.06346
ENSMUSG00000018042   20.57489   20.57251   20.62587   20.60867   20.61441
ENSMUSG00000018068   15.86464   15.68900   16.12644   16.07778   15.74226
ENSMUSG00000018102   16.38310   16.47731   16.71590   16.49956   18.09176
ENSMUSG00000018126   11.89782   11.71186   11.12530   11.12582   11.62262
ENSMUSG00000018143   17.93304   18.00370   18.29224   18.32412   18.26812
ENSMUSG00000018160   17.66479   17.59242   18.05360   18.20400   17.71664
ENSMUSG00000018166   19.76213   19.809

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)




ENSMUSG00000007097   12.88465
ENSMUSG00000007107   11.61161
ENSMUSG00000007122   12.35430
ENSMUSG00000007207   13.20401
ENSMUSG00000007216   12.70299
ENSMUSG00000007279   11.61981
ENSMUSG00000007338   17.30623
ENSMUSG00000007379   13.58925
ENSMUSG00000007411   18.13453
ENSMUSG00000007458   20.78994
ENSMUSG00000007476   18.10255
ENSMUSG00000007480   11.11883
ENSMUSG00000007564   19.14872
ENSMUSG00000007570   14.56338
ENSMUSG00000007613   17.99734
ENSMUSG00000007617   14.95271
ENSMUSG00000007646   12.00136
ENSMUSG00000007653   11.11883
ENSMUSG00000007655   14.78036
ENSMUSG00000007656   18.46668
ENSMUSG00000007659   18.88603
ENSMUSG00000007670   18.91901
ENSMUSG00000007682   12.29353
ENSMUSG00000007739   18.84192
ENSMUSG00000007812   17.59603
ENSMUSG00000007815   19.82216
ENSMUSG00000007827   14.97243
ENSMUSG00000007850   20.49207
ENSMUSG00000007867   13.37775
ENSMUSG00000007877   11.61981
ENSMUSG00000007880   19.18132
ENSMUSG00000007888   12.77202
ENSMUSG00000007891   23.47845
ENSMUSG00

ENSMUSG00000015653   15.35780
ENSMUSG00000015656   22.23074
ENSMUSG00000015665   11.11883
ENSMUSG00000015668   17.15950
ENSMUSG00000015671   18.29344
ENSMUSG00000015672   16.92191
ENSMUSG00000015697   17.87824
ENSMUSG00000015709   12.27392
ENSMUSG00000015714   21.10264
ENSMUSG00000015733   19.22499
ENSMUSG00000015747   14.82090
ENSMUSG00000015748   15.98834
ENSMUSG00000015750   17.26366
ENSMUSG00000015755   19.70036
ENSMUSG00000015757   16.71139
ENSMUSG00000015759   18.56885
ENSMUSG00000015766   14.19488
ENSMUSG00000015776   17.65591
ENSMUSG00000015787   11.11883
ENSMUSG00000015790   17.42264
ENSMUSG00000015806   19.01126
ENSMUSG00000015812   12.61997
ENSMUSG00000015829   11.48052
ENSMUSG00000015837   22.51809
ENSMUSG00000015839   22.07048
ENSMUSG00000015843   12.19474
ENSMUSG00000015846   22.00242
ENSMUSG00000015850   15.01071
ENSMUSG00000015880   14.07289
ENSMUSG00000015889   16.63233
ENSMUSG00000015890   17.65232
ENSMUSG00000015937   18.58815
ENSMUSG00000015944   14.79347
ENSMUSG000

In [16]:
%%R
tcdd_dose_detail.vec.train <-
   tcdd_dose_detail_vec_tis_of_interest[training_indices]
tcdd_dose_detail.vec.test <-
   tcdd_dose_detail_vec_tis_of_interest[-training_indices]

# print(gtex_tissue_detail.vec.train)
print(length(unique(tcdd_dose_detail.vec.train)))

[1] 2


In [17]:
%%R
saveRDS(tcdd_dose_detail.vec.train,file=paste(OUT_DIR,"tcdd_dose_detail_vec_train0.03vs30_time_cross.Rds",sep=""))

In [18]:
%%R
cv_fold_indices <- caret::createFolds(tcdd_dose_detail.vec.train,
                                      k = N_FOLDS)

In [19]:
%%R
binary_tcdd_dose_annotations <- unique(tcdd_dose_detail.vec)
print(binary_tcdd_dose_annotations)

[1] 30.00  0.03


In [20]:
%%R
full_rxn_pca_results.nls <- list()
rxn_id_2_result_file_idx.nls <- list()

In [21]:
%%R
n_rxns <- length(rxns)
print(n_rxns)
result_idx <- 1
for(rxn_id_idx in seq(1:n_rxns)){
   rxn_id <- rxns[rxn_id_idx]
   rxn_pca <-
      prcomp(t(vst.count.mtx.train[rxn2ensembls.nls[[rxn_id]], ]), scale. = T)
   full_rxn_pca_results.nls[[rxn_id]] <- rxn_pca
   rxn_id_2_result_file_idx.nls[[rxn_id]] <- result_idx
   rxn_pca.nls[[rxn_id]] <-
      rxn_pca$x[, 1] # 1st principal component coordinate within this reaction-space for each sample
   if(mod(rxn_id_idx,100) == 0){
      print(paste("Processed ",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      flush.console()
   }
   if(mod(rxn_id_idx,1000) == 0){
      print(paste("Storing PCA objects containing reactions ",rxn_id_idx-1000,
                  "-",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      saveRDS(full_rxn_pca_results.nls,
              paste(OUT_DIR, "full_rxn_pca_results_nls",rxn_id_idx-1000,
                    "-",rxn_id_idx,"0.03vs30_time_cross.Rds", sep=""))
      full_rxn_pca_results.nls <- list()
      gc()
      result_idx <- result_idx + 1
   }
}

[1] 9825
[1] "Processed 100 of 9825 reactions (1%)..."
[1] "Processed 200 of 9825 reactions (2%)..."
[1] "Processed 300 of 9825 reactions (3.1%)..."
[1] "Processed 400 of 9825 reactions (4.1%)..."
[1] "Processed 500 of 9825 reactions (5.1%)..."
[1] "Processed 600 of 9825 reactions (6.1%)..."
[1] "Processed 700 of 9825 reactions (7.1%)..."
[1] "Processed 800 of 9825 reactions (8.2%)..."
[1] "Processed 900 of 9825 reactions (9.2%)..."
[1] "Processed 1000 of 9825 reactions (10.2%)..."
[1] "Storing PCA objects containing reactions 0-1000 of 9825 reactions (10.2%)..."
[1] "Processed 1100 of 9825 reactions (11.2%)..."
[1] "Processed 1200 of 9825 reactions (12.2%)..."
[1] "Processed 1300 of 9825 reactions (13.2%)..."
[1] "Processed 1400 of 9825 reactions (14.3%)..."
[1] "Processed 1500 of 9825 reactions (15.3%)..."
[1] "Processed 1600 of 9825 reactions (16.3%)..."
[1] "Processed 1700 of 9825 reactions (17.3%)..."
[1] "Processed 1800 of 9825 reactions (18.3%)..."
[1] "Processed 1900 of 9825 re

In [22]:
%%R
# store remaining PCA objects and removing from RAM
saveRDS(rxn_id_2_result_file_idx.nls,
        paste(OUT_DIR,"rxn_id_2_result_file_idx_nls0.03vs30_time_cross.Rds",sep=""))
saveRDS(full_rxn_pca_results.nls,
        paste(OUT_DIR, "full_rxn_pca_results_nls0.03vs30_time_cross.Rds", sep=""))
rm(full_rxn_pca_results.nls)
gc()

           used  (Mb) gc trigger  (Mb) max used  (Mb)
Ncells  6950301 371.2   13075682 698.4 11898194 635.5
Vcells 15944447 121.7   25842636 197.2 25842636 197.2


In [23]:
%%R
# compare informaction content of below files with pca plots or similar
saveRDS(rxn_pca.nls, paste(OUT_DIR, "rxn_pca_nls0.03vs30_time_cross.Rds", sep = ""))
saveRDS(vst.count.mtx.train,
        paste(OUT_DIR, "vst_count_mtx_train0.03vs30_time_cross.Rds", sep = ""))

In [24]:
%%R
for (cv_fold in names(cv_fold_indices)) {
  cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
}

In [25]:
%%R
# print(tissue_annotation)
# print(binary_tcdd_dose_annotations)
# print(paste("Processing tissue annotation:", tissue_annotation))
# print(length(binary_tcdd_dose_detail_vec.test.cv_test_list))
# print(sum(tcdd_dose_detail.vec.train.cv_test == tissue_annotation))
# print(length(rxns))

# binary_tcdd_dose_annotations <- c(0.00, 30.00, 0.01, 0.03, 0.10, 0.30, 1.00, 3.00, 10.00)

formatted_annotations <- format(binary_tcdd_dose_annotations, nsmall = 2)

formatted_annotations <- trimws(formatted_annotations)

binary_tcdd_dose_annotations <- formatted_annotations

print(binary_tcdd_dose_annotations)
for (annotation in binary_tcdd_dose_annotations) {
    print(annotation)
}

[1] "30.00" "0.03" 
[1] "30.00"
[1] "0.03"


In [26]:
%%R
# main loop
for (rxn_id_idx in seq(1:length(rxns))) {
   rxn_id <- rxns[rxn_id_idx]
   ensembl_ids <- rxn2ensembls.nls[[rxn_id]]
   
   mean_misclass_rate <- list()
   sum_ari <- 0

   for (cv_fold in names(cv_fold_indices)) {
      cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
      
      vst.count.mtx.train.cv_train <-
         vst.count.mtx.train[, -cur_cv_fold_indices] # 4/5ths of training features
      vst.count.mtx.train.cv_test <-
         vst.count.mtx.train[, cur_cv_fold_indices] # 1/5th of training features
      
      tcdd_dose_detail.vec.train.cv_train <-
         tcdd_dose_detail.vec.train[-cur_cv_fold_indices] # 4/5ths of training labels
      tcdd_dose_detail.vec.train.cv_test <-
         tcdd_dose_detail.vec.train[cur_cv_fold_indices] # 1/5th of training labels
      
#        print(length(vst.count.mtx.train.cv_train))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
       
      binary_tcdd_dose_detail_vec.test.cv_test_list <- list()
      for (tissue_annotation in binary_tcdd_dose_annotations) {
#          print(tcdd_dose_detail.vec.train.cv_test)
#          print("-------------")
#          print(tissue_annotation)
#          print(binary_tcdd_dose_detail_vec.test.cv_test_list)
         binary_tcdd_dose_detail_vec.test.cv_test_list[[as.character(tissue_annotation)]] <-
            (as.character(tcdd_dose_detail.vec.train.cv_test) == as.character(tissue_annotation))
      }
      
      cv_train.expr_mat <-
         t(vst.count.mtx.train.cv_train[ensembl_ids, ])
      cv_test.expr_mat <-
         t(vst.count.mtx.train.cv_test[ensembl_ids, ])
#        print(dim(cv_train.expr_mat))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
      
      rxn_knn_calls <- class::knn(train = cv_train.expr_mat,
                                  test = cv_test.expr_mat,
                                  cl = tcdd_dose_detail.vec.train.cv_train)
      
      # calculate & store adjusted rand index
      cur_ari <- pdfCluster::adj.rand.index(rxn_knn_calls,
                                            tcdd_dose_detail.vec.train.cv_test)
      sum_ari <- cur_ari + sum_ari
      
      # for each tissue, calculate misclassification rate
      for (tissue_annotation in binary_tcdd_dose_annotations) {
         cur_rxn_knn_calls <- (rxn_knn_calls == tissue_annotation)
            
         # calculate misclassification rate (https://stat.ethz.ch/pipermail/r-help/2011-September/288885.html)
         tab <- table(cur_rxn_knn_calls,
                      binary_tcdd_dose_detail_vec.test.cv_test_list[[tissue_annotation]])
        # print(tab)
         cur_misclass_rate <- 1 - sum(diag(tab)) / sum(tab)
        # print(paste("Misclass rate = 1 - ",sum(diag(tab))," / ",sum(tab)," = ", cur_misclass_rate,"...",sep=""))
         sum_misclass_rate <- cur_misclass_rate
         if (!is.null(mean_misclass_rate[[tissue_annotation]])) {
           sum_misclass_rate <- sum_misclass_rate + mean_misclass_rate[[tissue_annotation]]
         }
         mean_misclass_rate[[tissue_annotation]] <- sum_misclass_rate
      }
   }
   for(tissue_annotation in binary_tcdd_dose_annotations){
      mean_misclass_rate[[tissue_annotation]] <- (mean_misclass_rate[[tissue_annotation]] / N_FOLDS)
   }
   mean_ari <- sum_ari / N_FOLDS
   ecount <- length(ensembl_ids)
   
   rxn_knn_misclass_rate.nls[[rxn_id]] <- mean_misclass_rate
   assign("mean_misclass_rate",NULL,envir = .GlobalEnv)
   
   rxn_knn_ari.nls[[rxn_id]] <- mean_ari
   rxn_knn_ecount.nls[[rxn_id]] <- ecount
   
   count <- count + 1
   if (mod(count, 10) == 0) {
      print(
         paste(
            "Last RXN_ID = ",
            rxn_id,
            ": Last ARI = ",
            mean_ari,
            ": Last ECOUNT = ",
            ecount,
            ": Last Lung MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Lung"]],
            ": Last Uterus MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Uterus"]],
            ". Now ",
            round(1.0 - count / length(rxns),3) * 100,
            "% remaining..."
         )
      )
      flush.console()
   }
}

[1] "Last RXN_ID =  R-MMU-749456 : Last ARI =  1 : Last ECOUNT =  178 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9021601 : Last ARI =  1 : Last ECOUNT =  24 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3108203 : Last ARI =  0.904851330203443 : Last ECOUNT =  15 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9838627 : Last ARI =  0.498482016253363 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-193679 : Last ARI =  0.021523281875352 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-194544 : Last ARI =  0.183012004400997 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-3247837 : Last 

[1] "Last RXN_ID =  R-MMU-450580 : Last ARI =  1 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-6791222 : Last ARI =  1 : Last ECOUNT =  61 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9696268 : Last ARI =  1 : Last ECOUNT =  41 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-1912394 : Last ARI =  1 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-8936481 : Last ARI =  1 : Last ECOUNT =  77 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-9677051 : Last ARI =  0.955555555555555 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-5336403 : Last ARI =  0.959214501510574 : Last ECOUNT =  72 

[1] "Last RXN_ID =  R-MMU-174119 : Last ARI =  0.949295774647887 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-174224 : Last ARI =  0.955555555555555 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-3788708 : Last ARI =  1 : Last ECOUNT =  23 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-927830 : Last ARI =  0.949295774647887 : Last ECOUNT =  11 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-448955 : Last ARI =  0.733422758774871 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89 % remaining..."
[1] "Last RXN_ID =  R-MMU-200652 : Last ARI =  0.0929477849553841 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  88.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-96

[1] "Last RXN_ID =  R-MMU-9013004 : Last ARI =  1 : Last ECOUNT =  16 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-9818576 : Last ARI =  0.0599116122139838 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84 % remaining..."
[1] "Last RXN_ID =  R-MMU-2029273 : Last ARI =  0.955555555555555 : Last ECOUNT =  71 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-8850356 : Last ARI =  0.906060606060606 : Last ECOUNT =  11 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-1363303 : Last ARI =  0.901709401709402 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-188386 : Last ARI =  0.895449620801733 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.6 % remaining..."
[1] "Last RXN_ID =  R-MMU

[1] "Last RXN_ID =  R-NUL-9625422 : Last ARI =  0.693412457702623 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79 % remaining..."
[1] "Last RXN_ID =  R-MMU-1449633 : Last ARI =  1 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-211910 : Last ARI =  1 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3928646 : Last ARI =  0.877396319692392 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-8848484 : Last ARI =  0.955555555555555 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9022185 : Last ARI =  0.823280333224591 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-2032396 : Last AR

...

[1] "Last RXN_ID =  R-MMU-77342 : Last ARI =  0.266986299394305 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-449937 : Last ARI =  -0.00638474203417765 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-9718020 : Last ARI =  0.340948794943069 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-6806966 : Last ARI =  0.0359871357442498 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-140783 : Last ARI =  0.955555555555555 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-5696457 : Last ARI =  0.540626171599623 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.1 % remaining..."
[1] "Last 

[1] "Last RXN_ID =  R-MMU-9653592 : Last ARI =  0.279731586569356 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9668464 : Last ARI =  0.112062505249337 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-2454118 : Last ARI =  0.602592259968542 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-159425 : Last ARI =  0.864065831714017 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-6785607 : Last ARI =  0.67474787336951 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-6807224 : Last ARI =  0.317607381641109 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17 % remaining..."
[1] "Last RXN_

[1] "Last RXN_ID =  R-MMU-9027532 : Last ARI =  0.823280333224591 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-917888 : Last ARI =  0.582132547320186 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-6800315 : Last ARI =  0.144526440529432 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-200424 : Last ARI =  0.539873873411802 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-425822 : Last ARI =  0.10764242208978 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-8848873 : Last ARI =  0.77474787336951 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12 % remaining..."
[1] "Last RXN_ID 

[1] "Last RXN_ID =  R-MMU-139909 : Last ARI =  -0.0207781247978182 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-8851979 : Last ARI =  0.323339024043249 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-9704248 : Last ARI =  0.349775355748807 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-5629230 : Last ARI =  0.845954671306784 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-1482961 : Last ARI =  0.90947276579833 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7 % remaining..."
[1] "Last RXN_ID =  R-NUL-9830947 : Last ARI =  0.381102949837075 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  6.9 % remaining..."
[1] "Last RXN_ID =

[1] "Last RXN_ID =  R-MMU-6807055 : Last ARI =  0.692246330262035 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-1462039 : Last ARI =  0.189549860511349 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-3341294 : Last ARI =  0.443009421450072 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-8952128 : Last ARI =  0.675157381009792 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2 % remaining..."
[1] "Last RXN_ID =  R-MMU-9606623 : Last ARI =  0.558123893420264 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  1.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-6814096 : Last ARI =  0.532340619138515 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  1.8 % remaining..."
[1] "Last RXN_ID =

In [27]:
%%R
saveRDS(
   rxn_knn_misclass_rate.nls,
   paste(OUT_DIR, "toi_rxn_knn_misclass_rate_nls0.03vs30_time_cross.Rds", sep = "")
)
saveRDS(rxn_knn_ari.nls,
        paste(OUT_DIR, "toi_rxn_knn_ari_nls0.03vs30_time_cross.Rds", sep = ""))
saveRDS(rxn_knn_ecount.nls,
        paste(OUT_DIR, "toi_rxn_knn_ecount_nls0.03vs30_time_cross.Rds", sep = ""))

In [28]:
%%R
d <- data.frame(
   RXN_ID = names(rxn2ensembls.nls),
   MISCLASS = unlist(rxn_knn_misclass_rate.nls),
   ARI = unlist(rxn_knn_ari.nls),
   ECOUNT = unlist(rxn_knn_ecount.nls)
)
print(d)
saveRDS(d, paste(OUT_DIR, "toi_summary_df0.03vs30_time_cross.Rds", sep = ""))

                           RXN_ID   MISCLASS           ARI ECOUNT
R-MMU-170666.30.00   R-MMU-170666 0.00000000  1.0000000000     14
R-MMU-170666.0.03    R-MMU-170671 0.00000000  1.0000000000     14
R-MMU-170671.30.00   R-MMU-170674 0.00000000  1.0000000000     14
R-MMU-170671.0.03    R-MMU-170686 0.00000000  1.0000000000     14
R-MMU-170674.30.00   R-MMU-380073 0.00000000  1.0000000000    182
R-MMU-170674.0.03    R-MMU-392187 0.00000000  0.9555555556     22
R-MMU-170686.30.00   R-MMU-392195 0.00000000  0.9555555556     22
R-MMU-170686.0.03    R-MMU-392202 0.00000000  0.9555555556     22
R-MMU-380073.30.00   R-MMU-749454 0.00000000  1.0000000000    178
R-MMU-380073.0.03    R-MMU-749456 0.00000000  1.0000000000    178
R-MMU-392187.30.00   R-MMU-751001 0.00000000  0.9555555556     21
R-MMU-392187.0.03   R-MMU-8964229 0.01111111  1.0000000000      5
R-MMU-392195.30.00  R-MMU-8964242 0.00000000  1.0000000000      5
R-MMU-392195.0.03   R-MMU-8964329 0.01111111  1.0000000000      5
R-MMU-3922

R-MMU-204981.0.03   R-MMU-5654165 0.07333333  1.0000000000     15
R-MMU-205060.30.00  R-MMU-5654167 0.00000000  1.0000000000     15
R-MMU-205060.0.03   R-MMU-5654169 0.03111111  1.0000000000     14
R-MMU-205099.30.00  R-MMU-5654222 0.00000000  1.0000000000     12
R-MMU-205099.0.03   R-MMU-5654224 0.03000000  1.0000000000     12
R-MMU-205112.30.00  R-MMU-5654392 0.00000000  1.0000000000     20
R-MMU-205112.0.03   R-MMU-5654397 0.01000000  0.9555555556     16
R-MMU-205117.30.00  R-MMU-5654399 0.00000000  0.9555555556     16
R-MMU-205117.0.03   R-MMU-5654402 0.06833333  0.9555555556     20
R-MMU-209532.30.00  R-MMU-5654404 0.00000000  0.9555555556     16
R-MMU-209532.0.03   R-MMU-5654406 0.40750000  0.9555555556     18
R-MMU-209566.30.00  R-MMU-5654407 0.00000000  0.9555555556     16
R-MMU-209566.0.03   R-MMU-5654408 0.02111111  0.9555555556     12
R-MMU-9012761.30.00 R-MMU-5654409 0.00000000  0.9555555556     12
R-MMU-9012761.0.03  R-MMU-5654413 0.04222222  1.0000000000     17
R-MMU-3247

R-MMU-5654165.0.03  R-MMU-2672334 0.00000000  0.6134199134      3
R-MMU-5654167.30.00 R-MMU-2682349 0.00000000  0.9555555556     14
R-MMU-5654167.0.03  R-MMU-9619662 0.00000000  0.2602265836      2
R-MMU-5654169.30.00 R-MMU-9619664 0.00000000  0.2602265836      2
R-MMU-5654169.0.03  R-MMU-9619682 0.00000000  1.0000000000      6
R-MMU-5654222.30.00 R-MMU-9010527 0.00000000  0.5640967678      3
R-MMU-5654222.0.03  R-MMU-9011075 0.00000000  0.4592764940      2
R-MMU-5654224.30.00 R-MMU-9011080 0.00000000  0.4203394556      2
R-MMU-5654224.0.03  R-MMU-9011082 0.00000000  0.4203394556      2
R-MMU-5654392.30.00 R-MMU-9011144 0.00000000  0.1008000943      3
R-MMU-5654392.0.03  R-MMU-9011146 0.00000000  0.1008000943      3
R-MMU-5654397.30.00 R-MMU-9753028 0.00000000  0.8954496208      5
R-MMU-5654397.0.03  R-MMU-9753126 0.01111111  0.8954496208      5
R-MMU-5654399.30.00  R-MMU-514604 0.00000000  0.5006451881      2
R-MMU-5654399.0.03   R-MMU-975389 0.01111111  0.2766493730      4
R-MMU-5654

R-MMU-5654646.0.03   R-MMU-205244 0.00000000  1.0000000000     11
R-MMU-5654647.30.00  R-MMU-205319 0.00000000  0.9555555556      8
R-MMU-5654647.0.03   R-MMU-210289 0.00000000  0.7899917576     11
R-MMU-5654651.30.00  R-MMU-210291 0.00000000  1.0000000000      6
R-MMU-5654651.0.03  R-MMU-2395412 0.00000000  0.7899917576     11
R-MMU-5654653.30.00 R-MMU-2395436 0.00000000  0.6817776128      4
R-MMU-5654653.0.03  R-MMU-2395801 0.00000000  0.8406959830     12
R-MMU-5654655.30.00 R-MMU-2396594 0.00000000  0.9555555556     19
R-MMU-5654655.0.03  R-MMU-2424480 0.00000000  0.9555555556     15
R-MMU-5654658.30.00 R-MMU-2424482 0.00000000  0.9555555556     15
R-MMU-5654658.0.03  R-MMU-2424484 0.00000000  0.9555555556     22
R-MMU-5654659.30.00 R-MMU-2424486 0.00000000  0.9555555556     22
R-MMU-5654659.0.03  R-MMU-2424487 0.00000000  0.9555555556     22
R-MMU-5654662.30.00  R-MMU-388814 0.00000000  0.5634724621      6
R-MMU-5654662.0.03   R-MMU-388829 0.00000000  1.0000000000      9
R-MMU-5654

R-MMU-2672334.0.03   R-MMU-418904 0.09777778  0.2450555576      2
R-MMU-2682349.30.00  R-MMU-164832 0.00000000  0.6944930546     18
R-MMU-2682349.0.03   R-MMU-164834 0.01111111  0.6944930546     18
R-MMU-9619662.30.00  R-MMU-164840 0.00000000  0.6944930546     18
R-MMU-9619662.0.03  R-MMU-8949580 0.22722222  0.6944930546     18
R-MMU-9619664.30.00 R-MMU-5626938 0.00000000  1.0000000000      6
R-MMU-9619664.0.03  R-MMU-8985343 0.22722222  0.4570997159      2
R-MMU-9619682.30.00 R-MMU-9690401 0.00000000  0.1032354007      2
R-MMU-9619682.0.03  R-MMU-9690410 0.00000000  0.1032354007      2
R-MMU-9010527.30.00 R-MMU-9690416 0.00000000  0.7491553055      4
R-MMU-9010527.0.03  R-MMU-9690868 0.11055556  0.1752993180      3
R-MMU-9011075.30.00 R-MMU-9690898 0.00000000  0.1752993180      3
R-MMU-9011075.0.03  R-MMU-9692133 0.14194444  0.0687392002      2
R-MMU-9011080.30.00 R-MMU-9692136 0.00000000  0.6144078144      2
R-MMU-9011080.0.03  R-MMU-9692137 0.15388889  0.8046521554      2
R-MMU-9011

...

R-NUL-9033304.0.03  R-MMU-8939959 0.17416667 -0.0550412747      1
R-NUL-9033333.30.00 R-MMU-2161791 0.00000000  1.0000000000      3
R-NUL-9033333.0.03  R-MMU-2161959 0.17416667  1.0000000000      3
R-MMU-443997.30.00  R-MMU-2161999 0.00000000  1.0000000000      3
R-MMU-443997.0.03   R-MMU-3341277 0.15666667  1.0000000000      1
R-MMU-391168.30.00  R-MMU-6805479 0.00000000  0.2057423977      2
R-MMU-391168.0.03   R-MMU-9614414 0.03222222  0.9601769912      3
R-MMU-8849638.30.00 R-MMU-9617657 0.00000000  0.6883082560      1
R-MMU-8849638.0.03  R-MMU-9617711 0.13416667  0.6883082560      1
R-MMU-8849646.30.00 R-MMU-9617755 0.00000000  0.6883082560      1
R-MMU-8849646.0.03  R-NUL-9617710 0.13416667  0.6883082560      1
R-MMU-1362465.30.00 R-NUL-9617742 0.00000000  0.6883082560      1
R-MMU-1362465.0.03  R-NUL-9617757 0.06722222  0.6883082560      1
R-MMU-112435.30.00  R-NUL-9617903 0.00000000  0.6883082560      1
R-MMU-112435.0.03   R-NUL-9617912 0.12000000  0.6883082560      1
R-MMU-9036

R-MMU-1855219.0.03  R-MMU-1482862 0.10666667  0.7359787012      5
R-MMU-2267372.30.00 R-MMU-1482897 0.00000000  0.7433414856      3
R-MMU-2267372.0.03  R-MMU-1482920 0.10666667  0.3939370459      2
R-MMU-994137.30.00  R-MMU-9794031 0.00000000  0.3101226606      1
R-MMU-994137.0.03    R-MMU-437240 0.10666667  0.6696436987      1
R-MMU-994140.30.00   R-MMU-140355 0.00000000  0.6970177070      1
R-MMU-994140.0.03    R-MMU-140359 0.10666667  0.6970177070      1
R-MMU-2467775.30.00 R-MMU-2314678 0.00000000  0.6970177070      1
R-MMU-2467775.0.03  R-MMU-9677320 0.15777778  0.6970177070      1
R-MMU-5223305.30.00 R-MMU-6803890 0.00000000  0.4958570565      1
R-MMU-5223305.0.03   R-MMU-947531 0.17277778  0.2995999760      1
R-MMU-8985201.30.00 R-MMU-5340195 0.00000000  0.5715169032      1
R-MMU-8985201.0.03  R-MMU-6806674 0.17277778  0.0745410354      1
R-MMU-196402.30.00   R-MMU-190681 0.00000000  0.3571681969      1
R-MMU-196402.0.03   R-MMU-9846477 0.08916667  0.4889253625      1
R-MMU-6807

R-MMU-5649764.0.03   R-MMU-163320 0.15500000 -0.0668998724      1
R-MMU-5649799.30.00 R-MMU-8851988 0.00000000  0.2805105243      1
R-MMU-5649799.0.03  R-MMU-6813749 0.15500000  0.3754655431      1
R-MMU-5649801.30.00   R-MMU-71691 0.00000000  0.3754655431      1
R-MMU-5649801.0.03   R-MMU-977348 0.15500000  0.5417171848      1
R-MMU-8847424.30.00  R-MMU-428961 0.00000000  0.7747478734      2
R-MMU-8847424.0.03  R-MMU-6807214 0.15305556  0.2630540197      2
R-MMU-561253.30.00   R-MMU-177784 0.00000000  0.0018342767      1
R-MMU-561253.0.03     R-MMU-71306 0.10083333  0.0018342767      1
R-MMU-428273.30.00  R-MMU-6797955 0.00000000  0.7751769428      1
R-MMU-428273.0.03     R-MMU-70941 0.05722222  0.7751769428      1
R-MMU-9836621.30.00  R-MMU-374207 0.00000000  0.3080296338      1
R-MMU-9836621.0.03  R-MMU-8980228 0.05722222  0.1204970280      1
R-MMU-428779.30.00  R-MMU-6787533 0.00000000  0.1116420345      1
R-MMU-428779.0.03   R-MMU-4084989 0.18888889  0.1882166501      1
R-MMU-8987

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)




R-MMU-159194.30.00  R-MMU-8955010 0.00000000 -0.0436852479      1
R-MMU-159194.0.03     R-MMU-71825 0.03222222  0.4293047022      1
R-MMU-9756134.30.00 R-MMU-5696146 0.00000000  0.4851890208      1
R-MMU-9756134.0.03  R-MMU-6788810 0.03222222  0.1056343894      1
R-MMU-9756156.30.00 R-MMU-8944246 0.00000000  0.5903396890      1
R-MMU-9756156.0.03   R-MMU-420384 0.03222222  0.3822466735      1
R-MMU-9756183.30.00 R-MMU-6786239 0.00000000  0.7148088023      1
R-MMU-9756183.0.03  R-MMU-9717434 0.03222222  0.3315935376      1
R-MMU-9632038.30.00 R-MMU-5619427 0.00000000  0.2805105243      1
R-MMU-9632038.0.03  R-MMU-1605723 0.29027778  0.0366220114      1
R-MMU-9632039.30.00 R-MMU-4085029 0.00000000  0.0366220114      1
R-MMU-9632039.0.03  R-MMU-8878787 0.29027778  0.6118291795      1
R-MMU-5695989.30.00  R-MMU-162821 0.00000000 -0.0345109916      1
R-MMU-5695989.0.03  R-MMU-5619433 0.05611111  0.2554678310      1
R-MMU-209821.30.00  R-MMU-6799977 0.00000000  0.9555555556      1
R-MMU-209

In [29]:
%%R
pid <- read.table(paste(OUT_DIR,"tcdd_project_id0.03vs30_time_cross.txt",sep=""),header=FALSE)
sid <- read.table(paste(OUT_DIR,"tcdd_sample_id0.03vs30_time_cross.txt",sep=""), header=FALSE)
sex <- read.table(paste(OUT_DIR, "tcdd_gender0.03vs30_time_cross.txt", sep=""), header=FALSE)
print(sex)

       V1
1    male
2    male
3    male
4    male
5    male
6    male
7    male
8    male
9    male
10   male
11   male
12   male
13   male
14   male
15   male
16   male
17   male
18   male
19   male
20   male
21   male
22   male
23   male
24   male
25   male
26   male
27   male
28   male
29   male
30   male
31   male
32   male
33   male
34   male
35   male
36   male
37   male
38   male
39   male
40   male
41   male
42   male
43   male
44   male
45   male
46   male
47   male
48   male
49 female
50 female
51 female
52 female
53 female
54 female
55 female
56 female
57 female
58 female
59 female
60 female
61 female
62 female
63 female
64 female
65 female
66 female
67 female
68 female
69 female
70 female
71 female
72 female
73 female
74 female
75 female
76 female
77 female
78 female
79 female
80   male
81   male
82   male
83   male
84   male
85   male
86   male
87   male
88   male
89   male
90   male
91   male


In [31]:
%%R
library(htmlwidgets)
min_misclass_pca <-
   prcomp(t(vst.count.mtx.train), scale. = T)
pca.d <- data.frame(
   PC1 = min_misclass_pca$x[, 1],
   PC2 = min_misclass_pca$x[, 2],
   PC3 = min_misclass_pca$x[, 3],
   Section = tcdd_dose_detail.vec.train,
   Project_id = pid$V1,
   Sample_id = sid$V1
)

ggplot(pca.d, aes(x = PC1, y = PC2, colour = Section)) +
   geom_point(size = 3) +  # 绘制点，指定点的大小
   geom_text(aes(label = paste(Project_id, Sample_id)), vjust = -1, hjust = 1, size = 2) +  # 添加标签
   scale_colour_manual(values = c("0.03" = "red", "30" = "green")) +  # 手动指定颜色
   theme_bw()

p <- plot_ly(
   data = pca.d,
   x = ~PC1,
   y = ~PC2,
   z = ~PC3,
   type = "scatter3d",
   mode = "markers",
   marker = list(
     color = as.factor(pca.d$Section),  # 将 Section 转换为因子
     colors = c("red", "green"),  # 定义颜色
     size = 5
   ),
   text = ~paste("Project ID:", Project_id, "Sample ID:", Sample_id)  # 在悬停文本中显示 Project ID
)
saveWidget(p, "plotly_chart0.03vs30_time_cross.html", selfcontained = TRUE)